In [207]:
import numpy as np
import pandas as pd
import nltk
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding,LSTM,Dense,Dropout,GRU
from sklearn.model_selection import train_test_split
from itertools import chain

In [110]:
train_data = pd.read_csv('train.csv')
test_data = pd.read_csv('test.csv')
train_data.head()

id keyword location                                               text  \
0   1     NaN      NaN  Our Deeds are the Reason of this #earthquake M...   
1   4     NaN      NaN             Forest fire near La Ronge Sask. Canada   
2   5     NaN      NaN  All residents asked to 'shelter in place' are ...   
3   6     NaN      NaN  13,000 people receive #wildfires evacuation or...   
4   7     NaN      NaN  Just got sent this photo from Ruby #Alaska as ...   

   target  
0       1  
1       1  
2       1  
3       1  
4       1

In [111]:
print('Train Data')
print('Sample size:',len(train_data))
print('\nNaN values:\n',train_data.isna().sum())
print('\nUnique values:')
print('keyword:',len(train_data['keyword'].unique()))
print('location:',len(train_data['location'].unique()))

train_data['keyword'] = train_data['keyword'].fillna('NoKeyword')
train_data['location'] = train_data['location'].fillna('NoLocation')

train_data['keyword'] = train_data['keyword'].str.lower()
train_data['location'] = train_data['location'].str.lower()
train_data['text'] = train_data['text'].str.lower()

Train Data
Sample size: 7613

NaN values:
 id             0
keyword       61
location    2533
text           0
target         0
dtype: int64

Unique values:
keyword: 222
location: 3342


In [112]:
print('Test Data')
print('Sample size:',len(test_data))
print('\nNaN values:\n',test_data.isna().sum())
print('\nUnique values:')
print('keyword:',len(test_data['keyword'].unique()))
print('location:',len(test_data['location'].unique()))

test_data['keyword'] = test_data['keyword'].fillna('NoKeyword')
test_data['location'] = test_data['location'].fillna('NoLocation')

test_data['keyword'] = test_data['keyword'].str.lower()
test_data['location'] = test_data['location'].str.lower()
test_data['text'] = test_data['text'].str.lower()

Test Data
Sample size: 3263

NaN values:
 id             0
keyword       26
location    1105
text           0
dtype: int64

Unique values:
keyword: 222
location: 1603


In [114]:
text_tokenizer = Tokenizer()
keyword_tokenizer = Tokenizer()
location_tokenizer = Tokenizer()

text_tokenizer.fit_on_texts(train_data['text'])
keyword_tokenizer.fit_on_texts(train_data['keyword'])
location_tokenizer.fit_on_texts(train_data['location'])

print('Vocabulary size:')
print('Text:',len(text_tokenizer.word_index)+1)
print('Keyword:',len(keyword_tokenizer.word_index)+1)
print('Location:',len(location_tokenizer.word_index)+1)

Vocabulary size:
Text: 22701
Keyword: 241
Location: 3325


In [196]:
text_input_sequences = []
for line in train_data['text']:
    # print(line)
    token_list = []
    tokens = text_tokenizer.texts_to_sequences(line)
    # print(tokens)
    for t in tokens:
        token_list += t
    text_input_sequences.append(token_list)

keyword_input_sequences = []
for line in train_data['keyword']:
    tokens = keyword_tokenizer.texts_to_sequences([line])[0]
    keyword_input_sequences.append(tokens)
        
location_input_sequences = []
for line in train_data['location']:
    tokens = location_tokenizer.texts_to_sequences([line])[0]
    location_input_sequences.append(tokens)
    
text_max_sequence_length = max([len(x) for x in text_input_sequences])
keyword_max_sequence_length = max([len(x) for x in keyword_input_sequences])
location_max_sequence_length = max([len(x) for x in location_input_sequences])

text_input_sequences = list(pad_sequences(text_input_sequences, maxlen=text_max_sequence_length, padding='pre'))
keyword_input_sequences = list(pad_sequences(keyword_input_sequences, maxlen=keyword_max_sequence_length, padding='pre'))
location_input_sequences = list(pad_sequences(location_input_sequences, maxlen=location_max_sequence_length, padding='pre'))

print(text_max_sequence_length, keyword_max_sequence_length, location_max_sequence_length)

124 3 12


In [206]:
print(text_input_sequences[0], keyword_input_sequences[0], location_input_sequences[0])

[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0  403   82
  566  400  579  579  400  107    5  566  579    1 1707  579  566  579
    5  107  403  402  403 1185    1 1707   10  107  579    5  566    1
 1707 3729   82    5 2032  579  283    5 3063    5 1427 1427    5 1707
 1185  403  566 1794   10 1129  579   82  107    5 1427 1427] [ 0  0 13] [0 0 0 0 0 0 0 0 0 0 0 1]


In [242]:
x = []
chain_len = text_max_sequence_length + keyword_max_sequence_length + location_max_sequence_length
for i in range(len(text_input_sequences)):
    x.append(list(chain(text_input_sequences[i], keyword_input_sequences[i], location_input_sequences[i])))
    # x.append([item for sublist in zip(text_input_sequences[i], keyword_input_sequences[i], location_input_sequences[i]) for item in sublist])
y = [[t] for t in train_data['target']]

In [243]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2)

In [251]:
np.matrix(x_train)

matrix([[   0,    0,    0, ...,    0,    0,    1],
        [   0,    0,    0, ...,    0,    0,    7],
        [   0,    0,    0, ...,    0,    0,    1],
        ...,
        [   0,    0,    0, ...,    0,  128,   55],
        [   0,    0,    0, ...,    0,    0,  153],
        [   0,    0,    0, ...,    0, 1949,    7]], dtype=int32)

In [245]:
early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)

In [254]:
model=Sequential([
Embedding(chain_len,250,input_length=chain_len),
LSTM(250,return_sequences=True),
Dropout(0.2),
LSTM(100),
Dense(1,activation="sigmoid")
])
model.compile(loss="categorical_crossentropy",optimizer='adam',metrics=['accuracy'])
model.summary()

/Users/ashvin.sehgal/AI-ML/.venv/lib/python3.12/site-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "sequential_5"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding_5 (Embedding)         │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_10 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_5 (Dropout)             │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_11 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ ?                      │   0 (unbuilt) │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 0 (0.00 B)

In [255]:
history=model.fit(x_train,y_train,epochs=50,validation_data=(x_test,y_test),verbose=1,callbacks=[early_stopping])

ValueError: Unrecognized data type: x=[[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 107, 403, 82, 1427, 1185, 403, 403, 400, 107, 403, 82, 402, 400, 107, 403, 506, 403, 283, 506, 566, 10, 1794, 1707, 1, 402, 403, 161, 73, 0, 0, 139, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 73, 1, 1707, 579, 566, 579, 161, 5, 107, 5, 107, 283, 5, 1427, 1427, 579, 5, 566, 1, 1707, 3729, 82, 5, 2032, 579, 10, 402, 1427, 5, 506, 82, 1, 400, 403, 402, 73, 1, 161, 403, 566, 566, 3063, 579, 283, 283, 3063, 566, 403, 107, 107, 82, 283, 10, 107, 1185, 10, 402, 579, 73, 0, 0, 33, 0, 0